In [2]:
!pip install transformers

import requests

import pandas as pd

from bs4 import BeautifulSoup

from datetime import datetime

import pandas as pd

import re

from transformers import pipeline

from google.colab import drive

import pandas as pd

from pandas.io.formats.info import pprint_thing

from google.colab import drive

drive.mount('/content/drive')



Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.1/7.1 MB 49.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 224.5/224.5 kB 23.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.8/7.8 MB 56.0 MB/s eta 0:00:00
Mounted at /content/drive


In [3]:
df10= pd.read_csv('/content/drive/MyDrive/DS105L/bbc/bbc_2010_2.csv')
df11= pd.read_csv('/content/drive/MyDrive/DS105L/bbc/bbc_2011_2.csv')
df12= pd.read_csv('/content/drive/MyDrive/DS105L/bbc/bbc_2012_2.csv')
df13= pd.read_csv('/content/drive/MyDrive/DS105L/bbc/bbc_2013_2.csv')
df14= pd.read_csv('/content/drive/MyDrive/DS105L/bbc/bbc_2014_2.csv')
df15= pd.read_csv('/content/drive/MyDrive/DS105L/bbc/bbc_2015_2.csv')






In [4]:
import requests
from bs4 import BeautifulSoup
from transformers import pipeline
import pandas as pd
from tqdm import tqdm

def assess_sentiment_model(text, model_name):
    sentiment_analyzer = pipeline("sentiment-analysis", model=model_name)
    result = sentiment_analyzer(text)
    sentiment = result[0]['label']
    score = result[0]['score']
    return sentiment, score

def get_bbc_content(url):
    r = requests.get(url)
    soup = BeautifulSoup(r.content, "html.parser") 
    content = soup.find("div", attrs={"class": "gel-layout__item gel-2/3@l"})
    
    if content is None:
        content = soup.find("td", attrs={"class": "storybody"})
        if content is None:
            return None

    main_body = content.find_all('p')
    text = ""
    for i in main_body:
        text += i.text
    clean_text = text.replace('\n', ' ').replace('\xa0', '')
    return clean_text


def preprocess_text(text):
    text = text.lower()     # Convert text to lowercase
    
    text = re.sub(r"[^\w\s]", "", text) # Remove punctuation and special characters
    
    words = nltk.word_tokenize(text)     # Tokenize the text into words

    stop_words = set(stopwords.words("english"))
    words = [word for word in words if word not in stop_words]
    
    preprocessed_text = " ".join(words)
    
    return preprocessed_text



def process_row(row, sentiment_models):
  
    content = get_bbc_content(row["url"])
    for model_name, sentiment_column in sentiment_models:
        sentiment_scores = []

        if content is not None:
            # Truncate or split the content into smaller chunks
            max_sequence_length = 512
            if len(content) > max_sequence_length:
                content_chunks = [content[i:i + max_sequence_length] for i in range(0, len(content), max_sequence_length)]
            else:
                content_chunks = [content]

            # Assess sentiment for each content chunk
            for chunk in content_chunks:
                sentiment, score = assess_sentiment_model(chunk, model_name)
                sentiment_scores.append(score)

        # Calculate average sentiment score
        if sentiment_scores:
            average_score = sum(sentiment_scores) / len(sentiment_scores)
            row[sentiment_column + "_average_score"] = average_score

    return row

def assess_sentiment(df):
    sentiment_models = [
        ("bert-base-uncased", "sentiment_bert"),
        ("xlnet-base-cased", "sentiment_xlnet")
    ]

    for _, sentiment_column in sentiment_models:
        df[sentiment_column + "_average_score"] = None

    total_rows = len(df)
    with tqdm(total=total_rows, desc="Processing Rows") as pbar:
        for index, row in df.iterrows():
            row = process_row(row, sentiment_models)
            df.loc[index] = row
            pbar.update(1)

            # Update progress bar description
            pbar.set_postfix({"Completed": index + 1})

    return df


In [5]:
import requests
from bs4 import BeautifulSoup
from transformers import pipeline
import pandas as pd
from tqdm import tqdm
from textblob import TextBlob
import nltk
nltk.download('punkt')
nltk.download('stopwords')
from nltk.corpus import stopwords
import re

def assess_sentiment_model(text, model_name):
    sentiment_analyzer = pipeline("sentiment-analysis", model=model_name)
    result = sentiment_analyzer(text)
    sentiment = result[0]['label']
    score = result[0]['score']
    return sentiment, score

def get_bbc_content(url):
    r = requests.get(url)
    soup = BeautifulSoup(r.content, "html.parser") 
    content = soup.find("div", attrs={"class": "gel-layout__item gel-2/3@l"})
    
    if content is None:
        content = soup.find("td", attrs={"class": "storybody"})
        if content is None:
            return None

    main_body = content.find_all('p')
    text = ""
    for i in main_body:
        text += i.text
    clean_text = text.replace('\n', ' ').replace('\xa0', '')
    return clean_text

def preprocess_text(text):
    text = text.lower()     # Convert text to lowercase
    
    text = re.sub(r"[^\w\s]", "", text) # Remove punctuation and special characters
    
    words = nltk.word_tokenize(text)     # Tokenize the text into words

    stop_words = set(stopwords.words("english"))
    words = [word for word in words if word not in stop_words]
    
    preprocessed_text = " ".join(words)
    
    return preprocessed_text

def process_row(row, sentiment_models):
    content = get_bbc_content(row["url"])
    if content is None:
        clean_text = preprocess_text(row['title'])
    else:
        clean_text = preprocess_text(content)
    
    for model_name, sentiment_column in sentiment_models:
        sentiment_scores = []

        if clean_text:
            max_sequence_length = 512
            if len(clean_text) > max_sequence_length:
                text_chunks = [clean_text[i:i + max_sequence_length] for i in range(0, len(clean_text), max_sequence_length)]
            else:
                text_chunks = [clean_text]

            for chunk in text_chunks:
                sentiment, score = assess_sentiment_model(chunk, model_name)
                sentiment_scores.append(score)

        if sentiment_scores:
            average_score = sum(sentiment_scores) / len(sentiment_scores)
            row[sentiment_column + "_average_score"] = average_score

    return row

def assess_sentiment(df):
    sentiment_models = [
        ("bert-base-uncased", "sentiment_bert"),
        ("xlnet-base-cased", "sentiment_xlnet")
    ]

    for _, sentiment_column in sentiment_models:
        df[sentiment_column + "_average_score"] = None

    total_rows = len(df)
    with tqdm(total=total_rows, desc="Processing Rows") as pbar:
        for index, row in df.iterrows():
            row = process_row(row, sentiment_models)
            df.loc[index] = row
            pbar.update(1)

            # Update progress bar description
            pbar.set_postfix({"Completed": index + 1})

    return df


[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.


In [23]:
df_10 = assess_sentiment(df10)
df_10.to_csv('/content/drive/MyDrive/DS105L/bbc/bbc_2010_4.csv', index=False)



Streaming output truncated to the last 5000 lines.
- This IS NOT expected if you are initializing XLNetForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of XLNetForSequenceClassification were not initialized from the model checkpoint at xlnet-base-cased and are newly initialized: ['logits_proj.bias', 'sequence_summary.summary.bias', 'logits_proj.weight', 'sequence_summary.summary.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of the model checkpoint at xlnet-base-cased were not used when initializing XLNetForSequenceClassification: ['lm_loss.bias', 'lm_loss.weight']
- This IS expected if you are initializing XLNetForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertF

In [ ]:
df_11 = assess_sentiment(df11)
df_11.to_csv('/content/drive/MyDrive/DS105L/bbc/bbc_2011_4.csv', index=False)



In [24]:
df_12 = assess_sentiment(df12)
df_12.to_csv('/content/drive/MyDrive/DS105L/bbc/bbc_2012_4.csv', index=False)



Streaming output truncated to the last 5000 lines.
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.weight', 'cls.seq_relationship.weight', 'cls.predictions.transform.dense.weight', 'cls.predictions.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias']

In [ ]:
df_13 = assess_sentiment(df13)
df_13.to_csv('/content/drive/MyDrive/DS105L/bbc/bbc_2013_4.csv', index=False)



In [26]:
df_14 = assess_sentiment(df14)
df_14.to_csv('/content/drive/MyDrive/DS105L/bbc/bbc_2014_4.csv', index=False)



Streaming output truncated to the last 5000 lines.
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.weight', 'cls.seq_relationship.weight', 'cls.predictions.transform.dense.weight', 'cls.predictions.bias', 'cls.seq_relationship.bias', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias']

In [6]:
df16= pd.read_csv('/content/drive/MyDrive/DS105L/bbc/bbc_2016_4.csv')



In [8]:
df17= pd.read_csv('/content/drive/MyDrive/DS105L/bbc/bbc_2017_2.csv')


In [9]:
df_16 = assess_sentiment(df16)
df_16.to_csv('/content/drive/MyDrive/DS105L/bbc/bbc_2016_4.csv', index=False)



Processing Rows:   0%|          | 0/187 [00:00<?, ?it/s]

Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.LayerNorm.weight', 'cls.seq_relationship.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.bias', 'cls.predictions.bias', 'cls.predictions.transform.dense.weight']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at

Xformers is not installed correctly. If you want to use memorry_efficient_attention to accelerate training use the following command to install Xformers
pip install xformers.
Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.LayerNorm.weight', 'cls.seq_relationship.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.bias', 'cls.predictions.bias', 'cls.predictions.transform.dense.weight']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a B

Some weights of the model checkpoint at xlnet-base-cased were not used when initializing XLNetForSequenceClassification: ['lm_loss.bias', 'lm_loss.weight']
- This IS expected if you are initializing XLNetForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing XLNetForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of XLNetForSequenceClassification were not initialized from the model checkpoint at xlnet-base-cased and are newly initialized: ['logits_proj.bias', 'logits_proj.weight', 'sequence_summary.summary.weight', 'sequence_summary.summary.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions a

Streaming output truncated to the last 5000 lines.
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.LayerNorm.weight', 'cls.seq_relationship.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.bias', 'cls.predictions.bias', 'cls.predictions.transform.dense.weight']

In [10]:
df_17 = assess_sentiment(df17)
df_17.to_csv('/content/drive/MyDrive/DS105L/bbc/bbc_2017_4.csv', index=False)



Streaming output truncated to the last 5000 lines.
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.LayerNorm.weight', 'cls.seq_relationship.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.bias', 'cls.predictions.bias', 'cls.predictions.transform.dense.weight']

In [11]:
df_11 = assess_sentiment(df11)
df_11.to_csv('/content/drive/MyDrive/DS105L/bbc/bbc_2011_4.csv', index=False)



Streaming output truncated to the last 5000 lines.
- This IS NOT expected if you are initializing XLNetForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of XLNetForSequenceClassification were not initialized from the model checkpoint at xlnet-base-cased and are newly initialized: ['logits_proj.bias', 'logits_proj.weight', 'sequence_summary.summary.weight', 'sequence_summary.summary.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
Some weights of the model checkpoint at xlnet-base-cased were not used when initializing XLNetForSequenceClassification: ['lm_loss.bias', 'lm_loss.weight']
- This IS expected if you are initializing XLNetForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertF

In [12]:
df_15 = assess_sentiment(df15)
df_15.to_csv('/content/drive/MyDrive/DS105L/bbc/bbc_2015_4.csv', index=False)



Processing Rows:   0%|          | 0/156 [00:00<?, ?it/s]Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForSequenceClassification: ['cls.predictions.transform.LayerNorm.weight', 'cls.seq_relationship.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.bias', 'cls.predictions.bias', 'cls.predictions.transform.dense.weight']
- This IS expected if you are initializing BertForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of BertForSequenceClassifi